In [1]:
import pandas as pd
from datetime import datetime
import numpy as np
from kerastuner.tuners import RandomSearch
from sklearn.preprocessing import MinMaxScaler
from tensorflow import keras
from tensorflow.keras import layers
# Load the TensorBoard notebook extension
%load_ext tensorboard
import tensorflow as tf
import datetime
from keras.callbacks import EarlyStopping

stopper = EarlyStopping(patience = 10)

# Clear any logs from previous runs
!rm -rf ./logs/ 

from kerastuner.tuners import RandomSearch

train_df = pd.read_csv('data/features_medium_provinces.csv')

train_df = train_df[train_df.metroscubiertos <= train_df.metrostotales]

train_x = train_df.drop(columns=['precio', 'usosmultiples'])
train_y = train_df.precio

scaler = MinMaxScaler(feature_range = (0,1))
coordinates_scaler = MinMaxScaler(feature_range = (-1, 1))

train_x.antiguedad = scaler.fit_transform(np.array(train_x.antiguedad).reshape(-1, 1))
train_x.metroscubiertos = scaler.fit_transform(np.array(train_x.metroscubiertos).reshape(-1, 1))
train_x.metrostotales = scaler.fit_transform(np.array(train_x.metrostotales).reshape(-1, 1))
train_x.habitaciones = scaler.fit_transform(np.array(train_x.habitaciones).reshape(-1, 1))
train_x.garages = scaler.fit_transform(np.array(train_x.garages).reshape(-1, 1))
train_x.banos = scaler.fit_transform(np.array(train_x.banos).reshape(-1, 1))

n_cols = train_x.shape[0]

train_x = train_x.to_numpy()
train_y = train_y.to_numpy()
#train_x.head()
train_x.shape

Using TensorFlow backend.


(16826, 31)

In [2]:
log_dir="logs/fit/medium_provinces/" + datetime.datetime.now().strftime("%Y%m%d-%H%M%S")
tensorboard_callback = tf.keras.callbacks.TensorBoard(log_dir = log_dir, histogram_freq=1)

In [3]:
def build_model(hp):
    model = keras.Sequential()
    model.add(layers.Dense(units=hp.Int('units_1', min_value=100, max_value=300, step=16), activation = 'relu', input_shape=(31,)))
    for i in range(hp.Int('num_layers', 3, 6)):
        model.add(layers.Dense(units=hp.Int('units_' + str(i),
                                            min_value=100,
                                            max_value=300,
                                            step=16),
                               activation='relu'))
    model.add(layers.Dense(1))
    model.compile(
        optimizer=keras.optimizers.Adam(
            hp.Choice('learning_rate', [1e-2, 1e-3, 1e-4])),
        loss='mean_squared_error',
        metrics=['mae'])
    return model

In [4]:
tuner = RandomSearch(
    build_model,
    objective='mae',
    max_trials=100,
    executions_per_trial=1,
    directory='models/deep_model_medium_provinces',
    project_name='deep_learning_with_keras_tuner')

tuner.search_space_summary()

tuner.search(x=train_x,
             y=train_y,
             epochs=50,
             validation_split=0.5,
            callbacks = [tensorboard_callback, stopper])

tuner.results_summary()
%tensorboard --logdir logs/fit

Train on 8413 samples, validate on 8413 samples
Epoch 1/50
8413/8413 [==============================] - ETA: 2:11 - loss: 3996683599872.0000 - mae: 1426450.500 - ETA: 12s - loss: 3573087135930.1816 - mae: 1450022.000 - ETA: 5s - loss: 2740845850939.0771 - mae: 1236908.8750 - ETA: 3s - loss: 2156026589184.0000 - mae: 1035060.312 - ETA: 2s - loss: 1825195778820.8301 - mae: 927730.687 - ETA: 2s - loss: 1660655966869.6616 - mae: 883599.12 - ETA: 1s - loss: 1521884237345.2468 - mae: 830739.43 - ETA: 1s - loss: 1356172386125.9131 - mae: 773393.56 - ETA: 1s - loss: 1262698648865.8113 - mae: 743279.75 - ETA: 1s - loss: 1190106467532.8000 - mae: 714418.12 - ETA: 0s - loss: 1141074135498.5076 - mae: 692646.31 - ETA: 0s - loss: 1093452980057.9459 - mae: 675433.75 - ETA: 0s - loss: 1040613665936.4908 - mae: 655210.00 - ETA: 0s - loss: 1013315149732.4692 - mae: 642317.43 - ETA: 0s - loss: 986301372032.0000 - mae: 631989.3125 - ETA: 0s - loss: 964674061346.2966 - mae: 623178.687 - ETA: 0s - loss: 94

Epoch 8/50
8413/8413 [==============================] - ETA: 1s - loss: 161446133760.0000 - mae: 284149.312 - ETA: 0s - loss: 422447663104.0000 - mae: 410605.781 - ETA: 0s - loss: 444658712047.4839 - mae: 412521.406 - ETA: 0s - loss: 486442474973.8666 - mae: 425065.593 - ETA: 0s - loss: 490529286553.6000 - mae: 421401.187 - ETA: 0s - loss: 508915659748.3243 - mae: 428828.812 - ETA: 0s - loss: 507515067578.1818 - mae: 430638.000 - ETA: 0s - loss: 533368884492.4272 - mae: 435919.250 - ETA: 0s - loss: 524582783028.5128 - mae: 431802.093 - ETA: 0s - loss: 511204315292.3359 - mae: 427735.812 - ETA: 0s - loss: 528852798691.5555 - mae: 431169.937 - ETA: 0s - loss: 556555747958.1538 - mae: 435072.093 - ETA: 0s - loss: 556901720449.5059 - mae: 435722.968 - ETA: 0s - loss: 538075336814.7027 - mae: 431229.718 - ETA: 0s - loss: 540858852114.1010 - mae: 435112.562 - ETA: 0s - loss: 551144954242.4150 - mae: 437149.937 - ETA: 0s - loss: 536826060836.4089 - mae: 432551.250 - ETA: 0s - loss: 5352752259

Epoch 21/50
8413/8413 [==============================] - ETA: 1s - loss: 365942112256.0000 - mae: 400367.562 - ETA: 0s - loss: 356937586688.0000 - mae: 372615.437 - ETA: 0s - loss: 452832030861.2414 - mae: 400817.031 - ETA: 0s - loss: 432771983918.5455 - mae: 396821.500 - ETA: 0s - loss: 501727302566.1754 - mae: 403350.125 - ETA: 0s - loss: 474205694821.6986 - mae: 397872.343 - ETA: 0s - loss: 464566779252.3636 - mae: 399343.125 - ETA: 0s - loss: 462648008541.7822 - mae: 399861.031 - ETA: 0s - loss: 472557975534.1913 - mae: 405441.593 - ETA: 0s - loss: 475345707946.0153 - mae: 406164.406 - ETA: 0s - loss: 490585958103.3931 - mae: 413438.156 - ETA: 0s - loss: 499257113696.6038 - mae: 418001.125 - ETA: 0s - loss: 480381596401.2874 - mae: 409708.218 - ETA: 0s - loss: 495729789697.3545 - mae: 413097.218 - ETA: 0s - loss: 497687581997.1765 - mae: 415857.187 - ETA: 0s - loss: 494360428130.6422 - mae: 414334.750 - ETA: 0s - loss: 494241916622.9787 - mae: 413514.250 - ETA: 0s - loss: 495401311

8413/8413 [==============================] - ETA: 1s - loss: 203054874624.0000 - mae: 317018.437 - ETA: 0s - loss: 616269484305.0667 - mae: 355681.937 - ETA: 0s - loss: 534476822235.4286 - mae: 373157.781 - ETA: 0s - loss: 459589782313.6744 - mae: 373965.937 - ETA: 0s - loss: 440445306125.4737 - mae: 380166.187 - ETA: 0s - loss: 499554502012.3428 - mae: 397197.406 - ETA: 0s - loss: 524265381598.8706 - mae: 409106.156 - ETA: 0s - loss: 492848577055.3469 - mae: 401417.312 - ETA: 0s - loss: 488471352173.7143 - mae: 402210.593 - ETA: 0s - loss: 476937713891.5555 - mae: 399601.125 - ETA: 0s - loss: 476952233704.0576 - mae: 401026.500 - ETA: 0s - loss: 467935649686.9744 - mae: 400775.750 - ETA: 0s - loss: 461131010993.2308 - mae: 398604.031 - ETA: 0s - loss: 456103649324.5217 - mae: 396237.968 - ETA: 0s - loss: 447529460959.5127 - mae: 394702.656 - ETA: 0s - loss: 440599160383.3905 - mae: 392407.281 - ETA: 0s - loss: 435132129463.6771 - mae: 390969.968 - ETA: 0s - loss: 436609497088.0000 - m

8413/8413 [==============================] - ETA: 1s - loss: 73932144640.0000 - mae: 214687.82 - ETA: 0s - loss: 323877896960.0000 - mae: 344082.156 - ETA: 0s - loss: 294981790614.0690 - mae: 339924.281 - ETA: 0s - loss: 344459304866.9091 - mae: 353478.625 - ETA: 0s - loss: 369753016424.1356 - mae: 363389.312 - ETA: 0s - loss: 386374629235.7260 - mae: 367693.125 - ETA: 0s - loss: 380764717940.3636 - mae: 367964.125 - ETA: 0s - loss: 370932761499.6078 - mae: 367859.968 - ETA: 0s - loss: 379046784463.8632 - mae: 371353.593 - ETA: 0s - loss: 410118847346.2154 - mae: 373294.812 - ETA: 0s - loss: 420193175637.3333 - mae: 376339.781 - ETA: 0s - loss: 414681529260.2767 - mae: 375855.062 - ETA: 0s - loss: 403517390071.1724 - mae: 372874.406 - ETA: 0s - loss: 405532430924.2553 - mae: 373181.656 - ETA: 0s - loss: 401462409368.8358 - mae: 373473.656 - ETA: 0s - loss: 399912690563.5888 - mae: 374634.906 - ETA: 0s - loss: 401682399502.6608 - mae: 375532.843 - ETA: 0s - loss: 400177666850.1334 - mae

...

8413/8413 [==============================] - ETA: 1s - loss: 204217991168.0000 - mae: 308112.750 - ETA: 1s - loss: 616321887883.6364 - mae: 440275.875 - ETA: 1s - loss: 707797747088.6957 - mae: 456785.187 - ETA: 1s - loss: 628270170580.1143 - mae: 445418.843 - ETA: 1s - loss: 573240135145.7391 - mae: 435478.312 - ETA: 0s - loss: 570493776231.2982 - mae: 438529.687 - ETA: 0s - loss: 569713410529.8823 - mae: 443194.000 - ETA: 0s - loss: 546528109062.4810 - mae: 440217.468 - ETA: 0s - loss: 521326951355.7333 - mae: 434589.906 - ETA: 0s - loss: 525764494285.3069 - mae: 433815.531 - ETA: 0s - loss: 508329620699.4286 - mae: 426475.062 - ETA: 0s - loss: 512346052977.3115 - mae: 425288.593 - ETA: 0s - loss: 523553252611.8209 - mae: 430229.250 - ETA: 0s - loss: 519486897441.5448 - mae: 428324.437 - ETA: 0s - loss: 517084661561.8065 - mae: 427638.687 - ETA: 0s - loss: 517261960105.6385 - mae: 429542.406 - ETA: 0s - loss: 519063085611.3898 - mae: 429302.656 - ETA: 0s - loss: 526521495769.8723 - m

8413/8413 [==============================] - ETA: 1s - loss: 171040833536.0000 - mae: 301117.812 - ETA: 1s - loss: 486066648405.3333 - mae: 407318.843 - ETA: 1s - loss: 496956945203.2000 - mae: 424739.875 - ETA: 1s - loss: 501460633372.4445 - mae: 431687.875 - ETA: 0s - loss: 512234799452.5958 - mae: 435701.781 - ETA: 0s - loss: 485565424032.5424 - mae: 422547.156 - ETA: 0s - loss: 516876112925.2571 - mae: 426956.437 - ETA: 0s - loss: 523221307341.4321 - mae: 426680.187 - ETA: 0s - loss: 501567289231.4725 - mae: 421688.250 - ETA: 0s - loss: 495083163131.0291 - mae: 420577.500 - ETA: 0s - loss: 500156630224.4248 - mae: 420074.250 - ETA: 0s - loss: 507658992398.5691 - mae: 421357.812 - ETA: 0s - loss: 493692604958.1177 - mae: 417102.156 - ETA: 0s - loss: 489806146720.2177 - mae: 417182.406 - ETA: 0s - loss: 489432319673.8854 - mae: 417126.281 - ETA: 0s - loss: 492678278396.9882 - mae: 417555.843 - ETA: 0s - loss: 496204568418.4615 - mae: 419795.156 - ETA: 0s - loss: 498405933269.3333 - m

8413/8413 [==============================] - ETA: 3s - loss: 325479596032.0000 - mae: 357342.156 - ETA: 1s - loss: 488092539289.6000 - mae: 415327.468 - ETA: 1s - loss: 430713402368.0000 - mae: 400184.718 - ETA: 1s - loss: 451832569856.0000 - mae: 418643.062 - ETA: 1s - loss: 445890107904.0000 - mae: 418245.093 - ETA: 1s - loss: 418316188833.6842 - mae: 409811.156 - ETA: 1s - loss: 476041251157.3333 - mae: 420463.968 - ETA: 1s - loss: 483762494358.0690 - mae: 419719.906 - ETA: 1s - loss: 502289292700.6567 - mae: 420590.406 - ETA: 1s - loss: 475618954146.9091 - mae: 411660.937 - ETA: 1s - loss: 462786638906.8506 - mae: 407417.343 - ETA: 0s - loss: 500293672049.7778 - mae: 409024.281 - ETA: 0s - loss: 500385603508.8441 - mae: 406171.187 - ETA: 0s - loss: 493324069225.4117 - mae: 405592.437 - ETA: 0s - loss: 517508037521.7231 - mae: 413312.406 - ETA: 0s - loss: 517318101136.2253 - mae: 414419.156 - ETA: 0s - loss: 513585497680.8421 - mae: 415771.093 - ETA: 0s - loss: 517773287019.4568 - m

INFO:tensorflow:Oracle triggered exit


Reusing TensorBoard on port 6006 (pid 13146), started 1 day, 17:14:57 ago. (Use '!kill 13146' to kill it.)

In [9]:
tuner.results_summary(200)

In [ ]:
tuned_model

In [22]:
best_models = tuner.get_best_models(num_models = 1)
best_model = best_models[0]

InvalidArgumentError: Unsuccessful TensorSliceReader constructor: Failed to get matching files on models/deep_model_medium_provinces/deep_learning_with_keras_tuner/trial_6d9854aab8b66703fbf3a7c1b0c78d0b/checkpoints/epoch_0/checkpoint: Not found: models/deep_model_medium_provinces/deep_learning_with_keras_tuner/trial_6d9854aab8b66703fbf3a7c1b0c78d0b/checkpoints/epoch_0; No such file or directory

In [ ]:
%tensorboard --logdir logs/fit

In [ ]:
# Best model params

#|-learning_rate: 0.001
#|-num_layers: 6
#|-units_0: 244
#|-units_1: 292
#|-units_2: 244
#|-units_3: 196
#|-units_4: 116
#|-units_5: 1
#|-Score: 399960.5625



In [ ]:
best_model_1 = models[0]

In [ ]:
best_model_2 = models[1]

In [ ]:
best_model_1.fit(train_x, train_y, epochs = 500, validation_split = 0.5, callbacks = [tensorboard_callback])

In [ ]:
%tensorboard --logdir logs/fit/medium_provinces

In [7]:
# Best model params
#|-learning_rate: 0.001
#|-num_layers: 6
#|-units_0: 276
#|-units_1: 276
#|-units_2: 148
##|-units_3: 164
#|-units_4: 228
#|-units_5: 276
#|-Score: 399960.5625

# Clear any logs from previous runs
!rm -rf ./logs/fit/medium_provinces

from keras.callbacks import EarlyStopping

stopper = EarlyStopping(patience = 15)

tuned_model = keras.Sequential()
tuned_model.add(layers.Dense(244, activation = 'relu', input_shape = (31,)))
tuned_model.add(layers.Dropout(0.5))
tuned_model.add(layers.Dense(292, activation = 'relu'))
tuned_model.add(layers.Dropout(0.5))
tuned_model.add(layers.Dense(244, activation = 'relu'))
tuned_model.add(layers.Dropout(0.5))
tuned_model.add(layers.Dense(164, activation = 'relu'))
tuned_model.add(layers.Dropout(0.5))
tuned_model.add(layers.Dense(196, activation = 'relu'))
tuned_model.add(layers.Dropout(0.5))
tuned_model.add(layers.Dense(116, activation = 'relu'))
tuned_model.add(layers.Dense(1))
tuned_model.compile(learning_rate = 0.01, loss = 'mean_squared_error', metrics = ['mae'])
tuned_model.fit(x=train_x, y=train_y, epochs=300, validation_split=0.5, callbacks = [tensorboard_callback, stopper])

%tensorboard --logdir logs/fit/medium_provinces/

Train on 8413 samples, validate on 8413 samples
Epoch 1/300
8413/8413 [==============================] - ETA: 3:49 - loss: 2625946779648.0000 - mae: 1334258.500 - ETA: 23s - loss: 3789437272064.0000 - mae: 1451371.250 - ETA: 12s - loss: 3535907751612.6313 - mae: 1439315.37 - ETA: 8s - loss: 3389072971281.6553 - mae: 1368762.6250 - ETA: 6s - loss: 2846710783568.8423 - mae: 1202361.000 - ETA: 5s - loss: 2581203472819.7446 - mae: 1123825.125 - ETA: 4s - loss: 2329300386654.3159 - mae: 1057291.750 - ETA: 3s - loss: 2155836806892.8955 - mae: 1008203.437 - ETA: 3s - loss: 2003268348011.7896 - mae: 969600.625 - ETA: 2s - loss: 1880968220767.2559 - mae: 932508.81 - ETA: 2s - loss: 1800774580565.3333 - mae: 909358.68 - ETA: 2s - loss: 1732720586829.2830 - mae: 885818.06 - ETA: 1s - loss: 1651437924210.7585 - mae: 859046.00 - ETA: 1s - loss: 1629429980533.8413 - mae: 846972.56 - ETA: 1s - loss: 1567267202783.7629 - mae: 832518.18 - ETA: 1s - loss: 1521227597131.9172 - mae: 818668.12 - ETA: 1s - 

8413/8413 [==============================] - ETA: 1s - loss: 580578574336.0000 - mae: 576409.875 - ETA: 1s - loss: 541739798900.3636 - mae: 446785.093 - ETA: 1s - loss: 736910580466.5264 - mae: 479118.531 - ETA: 1s - loss: 725066934766.3448 - mae: 485690.968 - ETA: 1s - loss: 676010910746.2565 - mae: 469698.343 - ETA: 1s - loss: 630285163039.3469 - mae: 467115.843 - ETA: 1s - loss: 621386819618.7119 - mae: 464291.750 - ETA: 1s - loss: 609428397723.8260 - mae: 465772.812 - ETA: 0s - loss: 626354684318.7848 - mae: 474710.125 - ETA: 0s - loss: 629322110722.8765 - mae: 477578.687 - ETA: 0s - loss: 618639101083.1515 - mae: 472202.218 - ETA: 0s - loss: 625327180358.4587 - mae: 473448.687 - ETA: 0s - loss: 601262387785.1428 - mae: 466340.562 - ETA: 0s - loss: 610420852544.0000 - mae: 469454.500 - ETA: 0s - loss: 623556097524.7883 - mae: 471663.562 - ETA: 0s - loss: 628985151878.0952 - mae: 474557.593 - ETA: 0s - loss: 625398152120.2548 - mae: 473078.687 - ETA: 0s - loss: 623458675583.2335 - m

Epoch 10/300
8413/8413 [==============================] - ETA: 1s - loss: 337989795840.0000 - mae: 453352.281 - ETA: 1s - loss: 473563968853.3333 - mae: 423608.218 - ETA: 1s - loss: 543410350266.1818 - mae: 439946.312 - ETA: 1s - loss: 524633173504.0000 - mae: 439232.531 - ETA: 1s - loss: 557203394060.4878 - mae: 450402.593 - ETA: 1s - loss: 541075770508.5490 - mae: 444327.812 - ETA: 1s - loss: 593004911547.7333 - mae: 446960.343 - ETA: 1s - loss: 590900008752.2319 - mae: 446682.375 - ETA: 0s - loss: 607182097032.1013 - mae: 450288.468 - ETA: 0s - loss: 637312293981.0909 - mae: 457131.093 - ETA: 0s - loss: 619845585381.6083 - mae: 454096.343 - ETA: 0s - loss: 615049515085.2830 - mae: 455330.718 - ETA: 0s - loss: 614953659668.0348 - mae: 459581.781 - ETA: 0s - loss: 613813483208.7040 - mae: 461837.375 - ETA: 0s - loss: 603497218903.8806 - mae: 459275.937 - ETA: 0s - loss: 598044750506.6666 - mae: 456309.406 - ETA: 0s - loss: 602707733038.5454 - mae: 460212.250 - ETA: 0s - loss: 60519475

Epoch 15/300
8413/8413 [==============================] - ETA: 1s - loss: 561584275456.0000 - mae: 516015.812 - ETA: 1s - loss: 523619064217.6000 - mae: 467668.156 - ETA: 1s - loss: 554089637790.4762 - mae: 475588.000 - ETA: 1s - loss: 541668825286.1935 - mae: 466768.656 - ETA: 1s - loss: 571070514790.4000 - mae: 468567.187 - ETA: 1s - loss: 566163537920.0000 - mae: 461790.906 - ETA: 1s - loss: 555922698311.8596 - mae: 455625.250 - ETA: 1s - loss: 588558154308.7761 - mae: 459020.000 - ETA: 1s - loss: 593272060442.9474 - mae: 462299.375 - ETA: 0s - loss: 616916209423.0588 - mae: 466035.156 - ETA: 0s - loss: 633197820744.7579 - mae: 467407.593 - ETA: 0s - loss: 635093498343.6190 - mae: 467479.656 - ETA: 0s - loss: 624866508515.0609 - mae: 463810.187 - ETA: 0s - loss: 640523518214.1440 - mae: 468414.125 - ETA: 0s - loss: 635880491872.7111 - mae: 467977.718 - ETA: 0s - loss: 628059241479.0620 - mae: 467550.687 - ETA: 0s - loss: 655216684151.6884 - mae: 471113.406 - ETA: 0s - loss: 64987274

8413/8413 [==============================] - ETA: 2s - loss: 656153378816.0000 - mae: 448391.062 - ETA: 1s - loss: 524185145344.0000 - mae: 451381.625 - ETA: 1s - loss: 636829481518.5454 - mae: 466485.125 - ETA: 1s - loss: 655412188325.1613 - mae: 467798.250 - ETA: 1s - loss: 659519582307.9025 - mae: 478235.125 - ETA: 1s - loss: 660782070824.9600 - mae: 477187.875 - ETA: 1s - loss: 632790060431.1864 - mae: 471278.062 - ETA: 1s - loss: 611228085187.7646 - mae: 462986.687 - ETA: 0s - loss: 590544429989.2659 - mae: 457327.250 - ETA: 0s - loss: 606046610338.9091 - mae: 463064.312 - ETA: 0s - loss: 590256067024.4949 - mae: 457913.531 - ETA: 0s - loss: 571205693980.9811 - mae: 454592.906 - ETA: 0s - loss: 563087490365.7931 - mae: 452892.625 - ETA: 0s - loss: 583238488293.3760 - mae: 456412.187 - ETA: 0s - loss: 586599980267.1407 - mae: 459082.562 - ETA: 0s - loss: 575917655153.7778 - mae: 457142.937 - ETA: 0s - loss: 567879450517.6104 - mae: 454078.187 - ETA: 0s - loss: 564973684985.7561 - m

...

Epoch 128/300
8413/8413 [==============================] - ETA: 1s - loss: 175671607296.0000 - mae: 299766.468 - ETA: 1s - loss: 474326482944.0000 - mae: 406542.531 - ETA: 1s - loss: 444276940409.9048 - mae: 413284.468 - ETA: 1s - loss: 455641882059.0345 - mae: 413530.250 - ETA: 1s - loss: 432313831424.0000 - mae: 405764.156 - ETA: 1s - loss: 428298677519.6735 - mae: 408444.625 - ETA: 1s - loss: 490236740278.2373 - mae: 421942.718 - ETA: 1s - loss: 504580333568.0000 - mae: 427434.156 - ETA: 0s - loss: 492542119014.4000 - mae: 425923.437 - ETA: 0s - loss: 481325917816.8090 - mae: 421871.687 - ETA: 0s - loss: 474535445065.1429 - mae: 420221.718 - ETA: 0s - loss: 474217411823.2523 - mae: 418873.156 - ETA: 0s - loss: 452494235127.3220 - mae: 412116.250 - ETA: 0s - loss: 456959521703.3071 - mae: 412417.281 - ETA: 0s - loss: 458968390484.0876 - mae: 413177.156 - ETA: 0s - loss: 476010729444.1360 - mae: 417748.093 - ETA: 0s - loss: 492273693039.5897 - mae: 420938.031 - ETA: 0s - loss: 4982529

Epoch 133/300
8413/8413 [==============================] - ETA: 1s - loss: 209614831616.0000 - mae: 335536.812 - ETA: 1s - loss: 509683802856.7273 - mae: 447022.031 - ETA: 1s - loss: 486051072970.1053 - mae: 425616.593 - ETA: 1s - loss: 459954904523.0345 - mae: 408433.781 - ETA: 1s - loss: 504185355641.2632 - mae: 414362.312 - ETA: 1s - loss: 466559621461.3333 - mae: 404521.093 - ETA: 1s - loss: 485966556195.3104 - mae: 408967.250 - ETA: 1s - loss: 499117658593.8823 - mae: 410022.750 - ETA: 1s - loss: 509273190665.9740 - mae: 412829.125 - ETA: 0s - loss: 506032619424.7442 - mae: 414347.031 - ETA: 0s - loss: 509065921109.3333 - mae: 418009.875 - ETA: 0s - loss: 514665895643.4286 - mae: 422573.750 - ETA: 0s - loss: 505652983790.1913 - mae: 420382.406 - ETA: 0s - loss: 514369895727.1040 - mae: 422835.812 - ETA: 0s - loss: 553883655221.0963 - mae: 429166.125 - ETA: 0s - loss: 542998471333.9586 - mae: 426795.375 - ETA: 0s - loss: 538262189538.2710 - mae: 426183.312 - ETA: 0s - loss: 5380382

Epoch 138/300
8413/8413 [==============================] - ETA: 1s - loss: 291677831168.0000 - mae: 333189.562 - ETA: 1s - loss: 525189712554.6667 - mae: 420259.031 - ETA: 1s - loss: 600439662324.8695 - mae: 443683.187 - ETA: 1s - loss: 551172023016.7273 - mae: 425357.218 - ETA: 1s - loss: 519698479627.9070 - mae: 414206.500 - ETA: 1s - loss: 517624345580.6793 - mae: 419087.093 - ETA: 1s - loss: 521841721856.0000 - mae: 415385.531 - ETA: 0s - loss: 524088714987.2432 - mae: 418012.781 - ETA: 0s - loss: 566133081798.7765 - mae: 430754.687 - ETA: 0s - loss: 559970387213.4736 - mae: 430505.468 - ETA: 0s - loss: 554911571101.5385 - mae: 430835.125 - ETA: 0s - loss: 543536171497.3452 - mae: 429194.687 - ETA: 0s - loss: 543776811444.4590 - mae: 429184.218 - ETA: 0s - loss: 530235313245.0909 - mae: 425722.718 - ETA: 0s - loss: 537838791896.3380 - mae: 427903.593 - ETA: 0s - loss: 561891434930.0133 - mae: 431615.406 - ETA: 0s - loss: 558132108854.0621 - mae: 430453.875 - ETA: 0s - loss: 5579633

Epoch 143/300
8413/8413 [==============================] - ETA: 1s - loss: 462161477632.0000 - mae: 392161.656 - ETA: 1s - loss: 666912690995.2000 - mae: 439188.187 - ETA: 1s - loss: 570241912185.2632 - mae: 433741.375 - ETA: 1s - loss: 568130958018.2069 - mae: 437849.968 - ETA: 1s - loss: 521850410745.4359 - mae: 429880.718 - ETA: 1s - loss: 515367297536.0000 - mae: 421840.406 - ETA: 1s - loss: 524936875467.0345 - mae: 425195.375 - ETA: 1s - loss: 515943961248.4776 - mae: 426895.031 - ETA: 1s - loss: 505526556025.2632 - mae: 423973.468 - ETA: 1s - loss: 490255201557.0823 - mae: 420888.156 - ETA: 0s - loss: 469867453866.6667 - mae: 415386.125 - ETA: 0s - loss: 468157604776.2286 - mae: 411510.968 - ETA: 0s - loss: 476175679991.0175 - mae: 413158.687 - ETA: 0s - loss: 468986007119.0894 - mae: 412262.156 - ETA: 0s - loss: 458611118911.5188 - mae: 410244.031 - ETA: 0s - loss: 461579154850.2535 - mae: 410004.031 - ETA: 0s - loss: 458347157544.6887 - mae: 409925.187 - ETA: 0s - loss: 4640053

Reusing TensorBoard on port 6007 (pid 26655), started 2 days, 21:35:31 ago. (Use '!kill 26655' to kill it.)

In [ ]:
%tensorboard --logdir logs/fit/medium_provinces/

In [17]:
prediction = tuned_model.predict(train_x)
from sklearn.metrics import mean_absolute_error
mean_absolute_error(prediction, train_y)

391931.96561404224

In [8]:
# serialize model to JSON
model_json = tuned_model.to_json()
with open("tuned_model_medium_provinces.json", "w") as json_file:
    json_file.write(model_json)
# serialize weights to HDF5
tuned_model.save_weights("model_medium_provinces.h5")
print("Saved model to disk")

Saved model to disk


In [21]:
best_model_prediction = best_model.predict(train_y)
mean_absolute_error(best_model_prediction, train_y)

NameError: name 'best_model' is not defined